# NAS-Bench-201 Exploration


In [1]:
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
import numpy as np

from bokeh.io import output_notebook, show, save
from bokeh.models import Range1d, Circle, ColumnDataSource, MultiLine
from bokeh.plotting import figure
from bokeh.plotting import from_networkx
from bokeh.palettes import Viridis256
from bokeh.transform import linear_cmap

output_notebook()

Loading BokehJS ...

Load in the adjacency matrix:

In [2]:
G = nx.from_numpy_matrix(
    np.load("minibench_nasbench201_distance_matrix.npy")
)

Get an ID and accuracy associated to each node:

In [3]:
df: pd.DataFrame = pd.read_pickle("minibench/mini-bench-arch-cell-accs.pd")

arch_ids = []
accuracies = []

for i in range(len(G)):
    G.nodes[i].update({"arch": df.iloc[i]["arch"], "acc": df.iloc[i]["cifar10-test"]})

Configure the plot:

In [4]:
title = "NAS-Bench-201"
colour_palette = Viridis256

HOVER_TOOLTIPS = [("Architecture ID", "@arch"),
                  ("CIFAR-10 Test Acc.", "@acc")]


plot = figure(tooltips=HOVER_TOOLTIPS, tools="pan,wheel_zoom,save,reset", active_scroll='wheel_zoom',)

network_graph = from_networkx(G, nx.spring_layout, scale=10, center=(0, 0))

minimum_value_color = min(network_graph.node_renderer.data_source.data['acc'])
maximum_value_color = max(network_graph.node_renderer.data_source.data['acc'])

network_graph.node_renderer.glyph = Circle(size=8, fill_color=linear_cmap('acc', colour_palette, minimum_value_color, maximum_value_color))
network_graph.edge_renderer.glyph = MultiLine(line_alpha=0., line_width=0.00001)

plot.renderers.append(network_graph)

show(plot)